# Eat Safe, Love

## Part 1: Database and Jupyter Notebook Set Up

Import the data provided in the `establishments.json` file from your Terminal. Name the database `uk_food` and the collection `establishments`.

Within this markdown cell, copy the line of text you used to import the data from your Terminal. This way, future analysts will be able to repeat your process.

e.g.: Import the dataset with `mongoimport --type json -d uk_food -c establishments --jsonArray establishments.json'

In [1]:
# Import dependencies
from pymongo import MongoClient
from pprint import pprint
from decimal import Decimal
from bson.decimal128 import Decimal128

In [2]:
# Create an instance of MongoClient
mongo = MongoClient(port=27017)

In [3]:
# confirm that our new database was created
dbs = mongo.list_database_names()
print(dbs)

['admin', 'config', 'local', 'travel_db', 'uk_food']


In [4]:
# assign the uk_food database to a variable name
db = mongo['uk_food']

In [5]:
# review the collections in our new database
collections = db.list_collection_names()
print(collections)

['establishments']


In [6]:
# review a document in the establishments collection
establishments = db.establishments.find_one()
pprint(establishments)

{'AddressLine1': '1 The Droveway',
 'AddressLine2': 'St Margarets Bay',
 'AddressLine3': 'Kent',
 'AddressLine4': '',
 'BusinessName': 'FirstLight Bar & Café',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'ChangesByServerID': 0,
 'Distance': 4587.64041272672,
 'FHRSID': 1290215,
 'LocalAuthorityBusinessID': 'PI/000083029',
 'LocalAuthorityCode': '182',
 'LocalAuthorityEmailAddress': 'publicprotection@dover.gov.uk',
 'LocalAuthorityName': 'Dover',
 'LocalAuthorityWebSite': 'http://www.dover.gov.uk/',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'CT15 6DH',
 'RatingDate': '2020-11-09T00:00:00',
 'RatingKey': 'fhrs_5_en-gb',
 'RatingValue': '5',
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('66306922bbbd4011b7269875'),
 'geocode': {'latitude': '51.150625', 'longitude': '1.378231'},
 'links': [{'href': 'https://api.ratings.food.gov.uk/establishments/1290215',
            'rel': 'self'}],
 'meta': {'dataSource': None,
          'extractDate': '

In [7]:
# assign the collection to a variable
establishments = db['establishments']

## Part 2: Update the Database

1. An exciting new halal restaurant just opened in Greenwich, but hasn't been rated yet. The magazine has asked you to include it in your analysis. Add the following restaurant "Penang Flavours" to the database.

In [8]:
# Create a dictionary for the new restaurant data
new_halal_doc = {
    "BusinessName":"Penang Flavours",
    "BusinessType":"Restaurant/Cafe/Canteen",
    "BusinessTypeID":"",
    "AddressLine1":"Penang Flavours",
    "AddressLine2":"146A Plumstead Rd",
    "AddressLine3":"London",
    "AddressLine4":"",
    "PostCode":"SE18 7DY",
    "Phone":"",
    "LocalAuthorityCode":"511",
    "LocalAuthorityName":"Greenwich",
    "LocalAuthorityWebSite":"http://www.royalgreenwich.gov.uk",
    "LocalAuthorityEmailAddress":"health@royalgreenwich.gov.uk",
    "scores":{
        "Hygiene":"",
        "Structural":"",
        "ConfidenceInManagement":""
    },
    "SchemeType":"FHRS",
    "geocode":{
        "longitude":"0.08384000",
        "latitude":"51.49014200"
    },
    "RightToReply":"",
    "Distance":4623.9723280747176,
    "NewRatingPending":True
}

In [9]:
# Insert the new restaurant into the collection
db.establishments.insert_one(new_halal_doc)

InsertOneResult(ObjectId('66306a149745dbcbd0361d13'), acknowledged=True)

In [10]:
# Check that the new restaurant was inserted
db.establishments.find_one({"BusinessName": "Penang Flavours"})

{'_id': ObjectId('66306a149745dbcbd0361d13'),
 'BusinessName': 'Penang Flavours',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': '',
 'AddressLine1': 'Penang Flavours',
 'AddressLine2': '146A Plumstead Rd',
 'AddressLine3': 'London',
 'AddressLine4': '',
 'PostCode': 'SE18 7DY',
 'Phone': '',
 'LocalAuthorityCode': '511',
 'LocalAuthorityName': 'Greenwich',
 'LocalAuthorityWebSite': 'http://www.royalgreenwich.gov.uk',
 'LocalAuthorityEmailAddress': 'health@royalgreenwich.gov.uk',
 'scores': {'Hygiene': '', 'Structural': '', 'ConfidenceInManagement': ''},
 'SchemeType': 'FHRS',
 'geocode': {'longitude': '0.08384000', 'latitude': '51.49014200'},
 'RightToReply': '',
 'Distance': 4623.972328074718,
 'NewRatingPending': True}

2. Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the `BusinessTypeID` and `BusinessType` fields.

In [11]:
# Find the BusinessTypeID for "Restaurant/Cafe/Canteen" and return only the BusinessTypeID and BusinessType fields
result = db.establishments.find_one({"BusinessType": "Restaurant/Cafe/Canteen"}, {"BusinessTypeID": 1, "BusinessType": 1, "_id": 0})
print(result)

{'BusinessType': 'Restaurant/Cafe/Canteen', 'BusinessTypeID': 1}


3. Update the new restaurant with the `BusinessTypeID` you found.

In [12]:
# Update the new restaurant with the correct BusinessTypeID
# Find the 'BusinessTypeID' for "Restaurant/Cafe/Canteen"
business_type_query = {"BusinessType": "Restaurant/Cafe/Canteen"}
business_type_projection = {"BusinessTypeID": 1, "_id": 0}
business_type_result = db.establishments.find_one(business_type_query, business_type_projection)
restaurant_business_type_id = business_type_result["BusinessTypeID"]

# Update the "Penang Flavours" restaurant with the correct 'BusinessTypeID'
penang_flavours_query = {"BusinessName": "Penang Flavours"}
penang_flavours_update = {"$set": {"BusinessTypeID": restaurant_business_type_id}}
db.establishments.update_one(penang_flavours_query, penang_flavours_update)

UpdateResult({'n': 1, 'nModified': 1, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [13]:
# Confirm that the new restaurant was updated
updated_penang_flavours = db.establishments.find_one(penang_flavours_query)
pprint(updated_penang_flavours)

{'AddressLine1': 'Penang Flavours',
 'AddressLine2': '146A Plumstead Rd',
 'AddressLine3': 'London',
 'AddressLine4': '',
 'BusinessName': 'Penang Flavours',
 'BusinessType': 'Restaurant/Cafe/Canteen',
 'BusinessTypeID': 1,
 'Distance': 4623.972328074718,
 'LocalAuthorityCode': '511',
 'LocalAuthorityEmailAddress': 'health@royalgreenwich.gov.uk',
 'LocalAuthorityName': 'Greenwich',
 'LocalAuthorityWebSite': 'http://www.royalgreenwich.gov.uk',
 'NewRatingPending': True,
 'Phone': '',
 'PostCode': 'SE18 7DY',
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('66306a149745dbcbd0361d13'),
 'geocode': {'latitude': '51.49014200', 'longitude': '0.08384000'},
 'scores': {'ConfidenceInManagement': '', 'Hygiene': '', 'Structural': ''}}


4. The magazine is not interested in any establishments in Dover, so check how many documents contain the Dover Local Authority. Then, remove any establishments within the Dover Local Authority from the database, and check the number of documents to ensure they were deleted.

In [14]:
# Find how many documents have LocalAuthorityName as "Dover"
dover_count = db.establishments.count_documents({'LocalAuthorityName': 'Dover'})

# Print the result
print(f"Number of documents with LocalAuthorityName as 'Dover': {dover_count}")

Number of documents with LocalAuthorityName as 'Dover': 994


In [15]:
# Delete all documents where LocalAuthorityName is "Dover"
result = db.establishments.delete_many({"LocalAuthorityName": "Dover"})

# Print the number of documents deleted
print(f"Number of documents deleted: {result.deleted_count}")

Number of documents deleted: 994


In [16]:
# Check if any remaining documents include Dover
remaining_dover_count = db.establishments.count_documents({'LocalAuthorityName': 'Dover'})

# Print the result
print(f"Number of documents with LocalAuthorityName as 'Dover': {remaining_dover_count}")

Number of documents with LocalAuthorityName as 'Dover': 0


In [17]:
# Check that other documents remain with 'find_one'
remaining_document = db.establishments.find_one()

if remaining_document:
    print("Other documents remain in the collection:")
    print(remaining_document)
else:
    print("No documents remain in the collection.")

Other documents remain in the collection:
{'_id': ObjectId('66306922bbbd4011b7269b5a'), 'FHRSID': 1043695, 'ChangesByServerID': 0, 'LocalAuthorityBusinessID': 'PI/000073616', 'BusinessName': 'The Pavilion', 'BusinessType': 'Restaurant/Cafe/Canteen', 'BusinessTypeID': 1, 'AddressLine1': 'East Cliff Pavilion', 'AddressLine2': 'Wear Bay Road', 'AddressLine3': 'Folkestone', 'AddressLine4': 'Kent', 'PostCode': 'CT19 6BL', 'Phone': '', 'RatingValue': '5', 'RatingKey': 'fhrs_5_en-gb', 'RatingDate': '2018-04-04T00:00:00', 'LocalAuthorityCode': '188', 'LocalAuthorityName': 'Folkestone and Hythe', 'LocalAuthorityWebSite': 'http://www.folkestone-hythe.gov.uk', 'LocalAuthorityEmailAddress': 'foodteam@folkestone-hythe.gov.uk', 'scores': {'Hygiene': 5, 'Structural': 5, 'ConfidenceInManagement': 5}, 'SchemeType': 'FHRS', 'geocode': {'longitude': '1.195625', 'latitude': '51.083812'}, 'RightToReply': '', 'Distance': 4591.765489457773, 'NewRatingPending': False, 'meta': {'dataSource': None, 'extractDate

5. Some of the number values are stored as strings, when they should be stored as numbers.

Use `update_many` to convert `latitude` and `longitude` to decimal numbers.

In [18]:
# Change the data type from String to Decimal for longitude and latitude
for establishment in db.establishments.find():
    if 'geocode' in establishment:
        establishment['geocode']['longitude'] = Decimal128(str(establishment['geocode']['longitude']))
        establishment['geocode']['latitude'] = Decimal128(str(establishment['geocode']['latitude']))
        db.establishments.update_one(
            {'_id': establishment['_id']},
            {'$set': {'geocode': establishment['geocode']}}
        )

Use `update_many` to convert `RatingValue` to integer numbers.

In [19]:
# Set non 1-5 Rating Values to Null
non_ratings = ["AwaitingInspection", "Awaiting Inspection", "AwaitingPublication", "Pass", "Exempt"]
establishments.update_many({"RatingValue": {"$in": non_ratings}}, [ {'$set':{ "RatingValue" : None}} ])

UpdateResult({'n': 4091, 'nModified': 4091, 'ok': 1.0, 'updatedExisting': True}, acknowledged=True)

In [27]:
# Change the data type from String to Integer for RatingValue
# Find documents where RatingValue is not a valid integer
invalid_documents = db.establishments.find({"RatingValue": {"$not": {"$type": "int"}}})

# Convert cursor to list to iterate over documents
invalid_documents_list = list(invalid_documents)

# Print number of invalid documents
print("Number of documents with invalid RatingValue:", len(invalid_documents_list))

# Update valid documents to change the data type of RatingValue from string to integer
for document in invalid_documents_list:
    try:
        # Extract the RatingValue from the dictionary
        rating_value = int(document["RatingValue"]["$toInt"])
        db.establishments.update_one({"_id": document["_id"]}, {"$set": {"RatingValue": rating_value}})
    except (KeyError, ValueError):
        print("Invalid RatingValue in document:", document["_id"])

Number of documents with invalid RatingValue: 38786
Invalid RatingValue in document: 66306922bbbd4011b7269b5a
Invalid RatingValue in document: 66306922bbbd4011b7269b5b
Invalid RatingValue in document: 66306922bbbd4011b7269b5e
Invalid RatingValue in document: 66306922bbbd4011b7269b60
Invalid RatingValue in document: 66306922bbbd4011b7269b61
Invalid RatingValue in document: 66306922bbbd4011b7269b63
Invalid RatingValue in document: 66306922bbbd4011b7269b64
Invalid RatingValue in document: 66306922bbbd4011b7269b65
Invalid RatingValue in document: 66306922bbbd4011b7269b66
Invalid RatingValue in document: 66306922bbbd4011b7269b67
Invalid RatingValue in document: 66306922bbbd4011b7269b68
Invalid RatingValue in document: 66306922bbbd4011b7269b69
Invalid RatingValue in document: 66306922bbbd4011b7269b6a
Invalid RatingValue in document: 66306922bbbd4011b7269b6b
Invalid RatingValue in document: 66306922bbbd4011b7269b6c
Invalid RatingValue in document: 66306922bbbd4011b7269b6d
Invalid RatingValue 

In [28]:
# Check that the coordinates and rating value are now numbers
# Query the database to find documents with the updated RatingValue data type
updated_documents = db.establishments.find({})

# Iterate over the documents and print the data types of coordinates and RatingValue
for document in updated_documents:
    print("Document ID:", document["_id"])
    print("Latitude Data Type:", type(document["geocode"]["latitude"]))
    print("Longitude Data Type:", type(document["geocode"]["longitude"]))
    print("RatingValue Data Type:", type(document["RatingValue"]))
    print("-------------------")

Document ID: 66306922bbbd4011b7269b5a
Latitude Data Type: <class 'bson.decimal128.Decimal128'>
Longitude Data Type: <class 'bson.decimal128.Decimal128'>
RatingValue Data Type: <class 'dict'>
-------------------
Document ID: 66306922bbbd4011b7269b5b
Latitude Data Type: <class 'bson.decimal128.Decimal128'>
Longitude Data Type: <class 'bson.decimal128.Decimal128'>
RatingValue Data Type: <class 'dict'>
-------------------
Document ID: 66306922bbbd4011b7269b5e
Latitude Data Type: <class 'bson.decimal128.Decimal128'>
Longitude Data Type: <class 'bson.decimal128.Decimal128'>
RatingValue Data Type: <class 'dict'>
-------------------
Document ID: 66306922bbbd4011b7269b60
Latitude Data Type: <class 'bson.decimal128.Decimal128'>
Longitude Data Type: <class 'bson.decimal128.Decimal128'>
RatingValue Data Type: <class 'dict'>
-------------------
Document ID: 66306922bbbd4011b7269b61
Latitude Data Type: <class 'bson.decimal128.Decimal128'>
Longitude Data Type: <class 'bson.decimal128.Decimal128'>
Rat

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

